In [1]:
import numpy as np
import time
from scipy.linalg import det as scipy_det
from sympy import Matrix
import matplotlib.pyplot as plt

In [3]:
def volume_cal(s_01, s_02, s_12, s_03, s_13, s_23):
    s_01_squared = s_01**2
    s_02_squared = s_02**2
    s_12_squared = s_12**2
    s_03_squared = s_03**2
    s_13_squared = s_13**2
    s_23_squared = s_23**2

    squared_vol = (
        4 * s_01_squared * s_02_squared * s_03_squared
        + (s_01_squared + s_02_squared - s_12_squared)
        * (s_01_squared + s_03_squared - s_13_squared)
        * (s_02_squared + s_03_squared - s_23_squared)
        - s_01_squared * ((s_02_squared + s_03_squared - s_23_squared) ** 2)
        - s_02_squared * ((s_01_squared + s_03_squared - s_13_squared) ** 2)
        - s_03_squared * ((s_01_squared + s_02_squared - s_12_squared) ** 2)
    )

    return squared_vol


def cayley_menger_matrix(s_01, s_02, s_12, s_03, s_13, s_23):
    matrix = np.array(
        [
            [0, 1, 1, 1, 1],
            [1, 0, s_01**2, s_02**2, s_03**2],
            [1, s_01**2, 0, s_12**2, s_13**2],
            [1, s_02**2, s_12**2, 0, s_23**2],
            [1, s_03**2, s_13**2, s_23**2, 0],
        ]
    )
    return matrix

In [12]:
s_01, s_02, s_12, s_03, s_13, s_23 = map(int, np.random.randint(0, 10000, 6))

In [13]:
volume_cal(s_01, s_02, s_12, s_03, s_13, s_23) * 2

138074921217974093488128

In [14]:
matrix = cayley_menger_matrix(s_01, s_02, s_12, s_03, s_13, s_23)

In [15]:
np.linalg.det(matrix)

np.float64(1.3807492121797437e+23)

In [2]:
from scipy.optimize import fsolve
import numpy as np


def volume_cal(s_01, s_02, s_12, s_03, s_13, s_23):
    s_01_squared = s_01**2
    s_02_squared = s_02**2
    s_12_squared = s_12**2
    s_03_squared = s_03**2
    s_13_squared = s_13**2
    s_23_squared = s_23**2

    squared_vol = (
        4 * s_01_squared * s_02_squared * s_03_squared
        + (s_01_squared + s_02_squared - s_12_squared)
        * (s_01_squared + s_03_squared - s_13_squared)
        * (s_02_squared + s_03_squared - s_23_squared)
        - s_01_squared * ((s_02_squared + s_03_squared - s_23_squared) ** 2)
        - s_02_squared * ((s_01_squared + s_03_squared - s_13_squared) ** 2)
        - s_03_squared * ((s_01_squared + s_02_squared - s_12_squared) ** 2)
    )

    return squared_vol


def find_s23(s_01, s_02, s_12, s_03, s_13, target_volume):
    def func(s_23):
        # volume_sq = volume(s_01, s_02, s_12, s_03, s_13, s_23)
        volume_sq = (
            (2 * s_01 * s_02 * s_03) ** 2
            + (s_01**2 + s_02**2 - s_12**2)
            * (s_01**2 + s_03**2 - s_13**2)
            * (s_02**2 + s_03**2 - s_23**2)
            - (s_01**2) * (s_02**2 + s_03**2 - s_23**2) ** 2
            - (s_02**2) * (s_01**2 + s_03**2 - s_13**2) ** 2
            - (s_03**2) * (s_01**2 + s_02**2 - s_12**2) ** 2
        )
        # print(type(volume_sq))
        return volume_sq - target_volume

    # Initial guess for s_23 (can be adjusted based on the problem)
    initial_guess = np.mean([s_01, s_02, s_12, s_03, s_13])

    # Find the root using fsolve
    s_23_solution = fsolve(func, initial_guess)
    return s_23_solution[0]


# candidate = find_s23(221,135,127,104,124,128)
# print(candidate)
# print(volume_cal(221,135,127,104,124,candidate))

In [ ]:
a = find_s23(221, 122, 118, 120, 111, 128)
volume_cal(221, 122, 118, 120, 111, a)

128.0

In [4]:
volume_cal(221, 128, 116, 121, 127, 108)

41218907175

In [ ]:
def process_s_01(s_01):
    results = []
    # print(f"Processing s_01 = {s_01}")
    for s_02 in range(1, s_01 + 1):
        for s_12 in range(max(s_01 - s_02, 1), s_02 + 1):
            if s_12 + s_02 > s_01:  # Triangle inequality for the base triangle
                base_area_squared = (
                    (s_01 + s_02 + s_12)
                    * (-s_01 + s_02 + s_12)
                    * (s_01 - s_02 + s_12)
                    * (s_01 + s_02 - s_12)
                    / 16
                )
                min_height = max(0, int(np.sqrt(8 / base_area_squared)) - 1)
                print("height:", min_height)
                for s_03 in range(min_height, s_02 + 1):  # Vertex 3 is the apex
                    for s_13 in range(max(min_height, s_01 - s_03 + 1), s_02 + 1):
                        # if s_13 + s_03 > s_01:
                        candidates = find_s23(s_01, s_02, s_12, s_03, s_13, 128)
                        # for s_23 in range(max(min_height, s_13-s_12+1, s_12-s_13+1, s_02-s_03+1), s_02 + 1):
                        for s_23 in [
                            int(candidates) - 1,
                            int(candidates),
                            int(candidates) + 1,
                        ]:
                            print(s_01, s_02, s_12, s_03, s_13, s_23)
                            # if (s_23 + s_03 > s_02) and (s_23 + s_13 > s_12):
                            vol = volume_cal(s_01, s_02, s_12, s_03, s_13, s_23)
                            if vol == 128:
                                results.append(
                                    (s_01, s_02, s_12, s_03, s_13, s_23, vol)
                                )
                                print(s_01, s_02, s_12, s_03, s_13, s_23, vol)
                            elif vol > 128:
                                break
    return results


s_01_values = range(221, 10000)
# s_01_values = range(0, 10000)

for s_01_value in s_01_values:
    print(s_01_value)
    process_s_01(s_01_value)

221
height: 0
221 111 111 111 111 1
height: 0
221 112 110 110 112 3
221 112 110 111 111 2
221 112 110 111 112 3
221 112 110 111 112 4
221 112 110 111 112 5
221 112 110 112 110 1
221 112 110 112 111 2
221 112 110 112 111 3
221 112 110 112 111 4
221 112 110 112 111 5
221 112 110 112 112 3
221 112 110 112 112 4
221 112 110 112 112 5
221 112 110 112 112 6
221 112 110 112 112 7
221 112 110 112 112 8
height: 0
221 112 111 110 112 3
221 112 111 110 112 4
221 112 111 110 112 5
221 112 111 111 111 2
221 112 111 111 111 3
221 112 111 111 111 4
221 112 111 111 111 5
221 112 111 111 112 2
221 112 111 112 110 2
221 112 111 112 110 3
221 112 111 112 110 4
221 112 111 112 110 5
221 112 111 112 111 1
221 112 111 112 112 2
221 112 111 112 112 3
221 112 111 112 112 4
height: 0
221 112 112 110 112 3
221 112 112 110 112 4
221 112 112 110 112 5
221 112 112 110 112 6
221 112 112 110 112 7
221 112 112 110 112 8
221 112 112 111 111 2
221 112 112 111 111 3
221 112 112 111 111 4
221 112 112 111 111 5
221 112 11

KeyboardInterrupt: 